### **AUTOMATION OF PROCESSING GPX TRACK RECORDS FOR DESIGNING INTENSITY MAPS**

The Map Matching algorithm runs on probabilistic model handling states with missing obseravation i.e., non-emitting states. For more information about the MM see [Leuven.MapMatching documentation](https://leuvenmapmatching.readthedocs.io/en/latest/classes/matcher/DistanceMatcher.html).

In [17]:
!jupyter nbextension enable --py --sys-prefix widgetsnbextension
!jupyter nbextension enable fileupload --user --py

Enabling notebook extension jupyter-js-widgets/extension...
      - Validating: OK
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/bin/jupyter-nbextension", line 10, in <module>
    sys.exit(main())
  File "/srv/conda/envs/notebook/lib/python3.10/site-packages/jupyter_core/application.py", line 277, in launch_instance
    return super().launch_instance(argv=argv, **kwargs)
  File "/srv/conda/envs/notebook/lib/python3.10/site-packages/traitlets/config/application.py", line 1043, in launch_instance
    app.start()
  File "/srv/conda/envs/notebook/lib/python3.10/site-packages/notebook/nbextensions.py", line 972, in start
    super().start()
  File "/srv/conda/envs/notebook/lib/python3.10/site-packages/jupyter_core/application.py", line 266, in start
    self.subapp.start()
  File "/srv/conda/envs/notebook/lib/python3.10/site-packages/notebook/nbextensions.py", line 882, in start
    self.toggle_nbextension_python(self.extra_args[0])
  File "/srv/conda/envs/notebook/lib

In [2]:
#!pip install ipywidgets
#!pip install --force-reinstall numpy==1.23
#!pip install pyproj
#!pip install gpx-converter
#!pip install geopandas
#!pip install git+https://github.com/wannesm/LeuvenMapMatching.git
#!pip install osmnx  # OpenStreetMap data access (built on top of the geopandas)
#!apt install libspatialindex-dev  # map visualization
#!pip install fiona rtree mapclassify  # map visualization
#!pip install leafmap  # map visualization

import ipywidgets as widget
#from IPython.display import display
from os.path import exists, join, basename
from os import listdir
from urllib.request import urlretrieve
import osmnx as ox
from shapely.geometry import Polygon, Point, LineString, box
from leuvenmapmatching.map.inmem import InMemMap
import numpy as np
import pandas as pd
import geopandas as gpd
from gpx_converter import Converter
from leuvenmapmatching.matcher.distance import DistanceMatcher
import leafmap.foliumap as leafmap

**Set Parameters**

In [3]:
DATA_UPLOAD = widget.FileUpload(
    accept='.gpx',
    multiple=True,
    description='Upload files'
)
PLACE_NAME = widget.Text(
    value='',
    placeholder='type your location',
    description='Study Area:'
)
BUFFER_DIST = widget.FloatSlider(
    value=0.005,
    min=0,
    max=0.01,
    step=0.001,
    description='Buffer',
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='.3f',
)
TOLERANCE = widget.FloatSlider(
    value=0.00004,
    min=0,
    max=0.0001,
    step=0.00001,
    description='Tolerance',
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='.5f',
)
MAX_DIST = widget.IntSlider(
    value=100,
    min=20,
    max=500,
    step=20,
    description='Max. Distance',
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
OBS_NOISE = widget.IntSlider(
    value=20,
    min=2,
    max=100,
    step=2,
    description='Obs. Noise',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
OBS_NOISE_NE = widget.IntSlider(
    value=60,
    min=5,
    max=200,
    step=5,
    description='Obs.Noise NE',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
DIST_NOISE = widget.IntSlider(
    value=5,
    min=1,
    max=25,
    step=1,
    description='Dist. Noise',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
DIST_NOISE_NE = widget.IntSlider(
    value=15,
    min=5,
    max=50,
    step=5,
    description='Dist.Noise NE',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
MAX_LATTICE_WIDTH = widget.IntSlider(
    value=7,
    min=1,
    max=15,
    step=1,
    description='Max Lattice',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
INCREASE_MAX_LATTICE_WIDTH = widget.IntSlider(
    value=2,
    min=1,
    max=5,
    step=1,
    description='Increase Latt.',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
MIN_PROB_NORM = widget.FloatSlider(
    value=0.005,
    min=0,
    max=1,
    step=0.001,
    description='Min Proba.',
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='.3f',
)

In [13]:
items = [DATA_UPLOAD, PLACE_NAME]
widget.GridBox(items, layout=widget.Layout(grid_template_columns="repeat(2, 200px)"))

GridBox(children=(FileUpload(value={'test_7.gpx': {'metadata': {'name': 'test_7.gpx', 'type': '', 'size': 2108…

In [1]:
#items = [BUFFER_DIST, TOLERANCE, MAX_DIST, MIN_PROB_NORM, OBS_NOISE, OBS_NOISE_NE, DIST_NOISE, 
#         DIST_NOISE_NE, MAX_LATTICE_WIDTH, INCREASE_MAX_LATTICE_WIDTH]
#widget.GridBox(items, layout=widget.Layout(grid_template_columns="repeat(2, 350px)"))

In [5]:
%%html
<style>
table {float:left}
</style>

|Parameter |Description |
|--------- |----------- |
|Buffer         |*expand the study area to minimise potential edge effect on the result; distance in degrees (WGS84)*|
|Tolerance      |*GPX track simplification threshold; distance in degrees (WGS84)*|
|Max. Distance  |*break for zero match probability; in meters*|
|Min. Proba.    |*stop matching below normalized probability*|
|Obs. Noise     |*standard deviation of measuremnet noise, in meter*|
|Obs. Noise NE  |*standard deviation of measuremnet noise for non-emitting states, in meter (the value should be larger than Obs. Noise)*|
|Dist. Noise    |*difference between distance between matched route and distance between tracks, in meter*|
|Dist. Noise Ne |*difference between the distances for non-emitting states, in meter (the value should be larger than Dist. Noise)*|
|Max Lattice    |*search the route with the number of possible paths at every step*|
|Increase Latt. |*if no solution is found, increase the lattice by the value*|

In [6]:
items = [widget.VBox([BUFFER_DIST, TOLERANCE]),
         widget.HBox([MAX_DIST, MIN_PROB_NORM]),
         widget.HBox([OBS_NOISE, OBS_NOISE_NE]),
         widget.HBox([DIST_NOISE, DIST_NOISE_NE]),
         widget.HBox([MAX_LATTICE_WIDTH, INCREASE_MAX_LATTICE_WIDTH])]
accordion = widget.Accordion(children=items)
accordion.set_title(0,"Environment Parameters")
accordion.set_title(1,"Thresholding of Matching")
accordion.set_title(2,"Observation Noise")
accordion.set_title(3,"Distance Noise")
accordion.set_title(4,"Probabilistic Lattice")
accordion

Accordion(children=(VBox(children=(FloatSlider(value=0.005, continuous_update=False, description='Buffer', max…

In [7]:
RUN_BUTTON = widget.Button(description='Run the Tool')
RUN_BUTTON

Button(description='Run the Tool', style=ButtonStyle())

In [18]:
for name, file_info in DATA_UPLOAD.value.items():
    content = DATA_UPLOAD.value[name]['content']
    print(content)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
## Set the directory location for data and output files
#DATA_FOLDER = 'data'
#OUTPUT_FOLDER = 'output'

## Study area for OpenStreetMap Street Network Download [1]
#PLACE_NAME = 'Olomouc, Czech Republic'  # extract data within the unit (area)
#BUFFER_DIST = 0.005  # minimise potential edge effect on the result; distance in degrees (EPSG:4326)

## Map Matching parameters. [2]
#TOLERANCE = 0.00004  # threshold for GPX track simplification; distance in degrees
#MAX_DIST = 100  # break for zero measurement (match) probability; in meters
#OBS_NOISE = 20  # expected GNSS noise, in meter
#OBS_NOISE_NE = 60  # expected GNSS noise for non-emitting states (the value should be larger than OBS_NOISE), in meter
#DIST_NOISE = 5  # difference between distance between matched route and distance between tracks, in meter
#DIST_NOISE_NE = 15  # difference between distances for non-emitting states, in meter
#MAX_LATTICE_WIDTH = 7  # search the route with this number of possible paths at every step
#INCREASE_MAX_LATTICE_WIDTH = 2  # if no solution is found, the width can be incremented by the value
#MIN_PROB_NORM = 0.005  # eliminate the lattice where it drops below normalized probability

In [15]:
study_area = ox.geocode_to_gdf(PLACE_NAME.value)
boundary_sa = gpd.GeoDataFrame(geometry=gpd.GeoSeries(study_area.boundary)) # for visualization purposes
gpx_concat = pd.DataFrame(columns=['latitude', 'longitude'])

for uploaded_filename in upload.value:
  content = upload.value[uploaded_filename]['content']   
  gpx_df = Converter(input_file = DATA_UPLOAD.data[i]).gpx_to_dataframe()
  gpx_concat = pd.concat([gpx_concat, gpx_df])

gpx_point = gpd.GeoDataFrame(gpx_concat, geometry=gpd.points_from_xy(gpx_concat.longitude, gpx_concat.latitude)).set_crs('epsg:4326')
gpx_clip = gpd.clip(gpx_point, study_area, keep_geom_type=True)

area_polygon = gpx_clip.buffer(BUFFER_DIST.value).set_crs(4326)
area_bounds = box(*area_polygon.total_bounds)

## Download graph based on netwotk type
## possible network types {"all_private", "all", "bike", "drive", "drive_service", "walk"}
graph = ox.graph_from_polygon(area_bounds, network_type='all', simplify=False)

#print(graph) # number of nodes and edges

del gpx_concat, gpx_point, gpx_clip, gpx_df

Exception: The file b'<?xml version="1.0" encoding="UTF-8"?>\n<gpx creator="StravaGPX" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.topografix.com/GPX/1/1 http://www.topografix.com/GPX/1/1/gpx.xsd" version="1.1" xmlns="http://www.topografix.com/GPX/1/1">\n <metadata>\n  <time>2017-11-03T17:31:36Z</time>\n </metadata>\n <trk>\n  <name>Takovej m\xc3\xadstn\xc3\xad hit tadyto - tak jsem to musel taky zkusit</name>\n  <type>9</type>\n  <trkseg>\n   <trkpt lat="49.5877480" lon="17.2552850">\n    <ele>216.0</ele>\n    <time>2017-11-03T17:31:36Z</time>\n   </trkpt>\n   <trkpt lat="49.5875700" lon="17.2551050">\n    <ele>215.2</ele>\n    <time>2017-11-03T17:31:43Z</time>\n   </trkpt>\n   <trkpt lat="49.5874070" lon="17.2547130">\n    <ele>214.8</ele>\n    <time>2017-11-03T17:31:57Z</time>\n   </trkpt>\n   <trkpt lat="49.5873810" lon="17.2542670">\n    <ele>215.7</ele>\n    <time>2017-11-03T17:32:07Z</time>\n   </trkpt>\n   <trkpt lat="49.5874990" lon="17

# **2. Map Matching**

### Leuven Map Object 
Create the in-memory representation of a map: translate graph(nodes, edges) to *InMemMap*. The strucutre represents the connectivity of the graph suggests the most possible transitions 

In [ ]:
map_con = InMemMap("road_network", 
                   use_latlon=True, 
                   use_rtree=True, 
                   index_edges=True)

for node in graph.nodes:
  lat = graph.nodes[node]['y']
  lon = graph.nodes[node]['x']
  map_con.add_node(node, (lat, lon))

for edge in graph.edges:
  node_a, node_b = edge[0], edge[1]
  map_con.add_edge(node_a, node_b)
  map_con.add_edge(node_b, node_a)

map_con.purge() # remove nodes without location or edges

## Iterate the algorithm over the GPX files


1.   Filter other files than with "*.gpx*" extension.
2.   Clip the GNSS measuremants with the studay area
3.   Move to the next file if outside of the study area.
5.   Retrieve coordinates from GNSS measurements and create a path and a track.
6.   Set the parametrization for the Leuven Map Matching algorithm. Run it over the path.
7.   Create a route from the nodes that the matched path passes through.
8.   Merge the pair of nodes (streets) into one DataFrame.



In [ ]:
track_df = pd.DataFrame(columns=['Latitude', 'Longitude','id'])
route_df = pd.DataFrame(columns=['Latitude', 'Longitude','id'])
id = 1

for filename in listdir(DATA_FOLDER):
  if not filename.endswith(".gpx"):
    continue
  
  print("Map matching of " + filename + " started...")
  gpx_df = Converter(input_file = DATA_FOLDER +"/"+ filename).gpx_to_dataframe()
  gpx_point = gpd.GeoDataFrame(gpx_df, geometry=gpd.points_from_xy(gpx_df.longitude, gpx_df.latitude)).set_crs('epsg:4326')
  gpx_point['id'] = 1
  
  gpx_clip = gpd.clip(gpx_point, area_polygon, keep_geom_type=True)
  if gpx_clip.empty:
    print("The GPX file is outside of the extent of study area. Map matching finished with no result.")
    print("---")
    continue
  
  gpx_clip = gpx_clip.sort_index()
  gpx_line = gpx_clip.groupby(['id']) ['geometry'].apply(lambda x: LineString(x.tolist()))
  line_gdf = gpd.GeoDataFrame(gpx_line, geometry='geometry').set_crs('epsg:4326')
  line_gdf['geometry'] = line_gdf['geometry'].simplify(TOLERANCE.value) # reducing line vertices inside the tolerance

  gpx_coords = line_gdf.apply(lambda row: list((row.geometry).coords), axis=1)

  for row in gpx_coords.items():
    passage = list(row[1:])
    passage = passage[0]
    track = []
    path = []
    
    for i in range(len(passage)):
      lat = passage[i][1]
      lon = passage[i][0]
      path.append((lat, lon)) 
      track.append([lat, lon])

    track = np.array(track)
    #print(path[:10]) # path is a list of tuples
    #print(track[:10]) # NumPy array; indexed coordinate pairs
    df = pd.DataFrame(track, columns=['Latitude', 'Longitude'])
    df['id'] = id # id for grouping into one line
    track_df = pd.concat([track_df, df])

  matcher = DistanceMatcher(map_con,
                            max_dist = MAX_DIST.value,
                            min_prob_norm = MIN_PROB_NORM.value,
                            max_lattice_width = MAX_LATTICE_WIDTH.value,
                            increase_max_lattice_width = INCREASE_MAX_LATTICE_WIDTH.value,
                            obs_noise = OBS_NOISE.value, 
                            obs_noise_ne = OBS_NOISE_NE.value,
                            dist_noise = DIST_NOISE.value,
                            dist_noise_ne = DIST_NOISE_NE.value,
                            non_emitting_edgeid=False,
                            restrained_ne = False)
    
  matcher.match(path, unique=False) # retain only unique nodes in the sequence (avoid repetitions)
  if matcher.early_stop_idx is not None:
    print("Parts of the path were omitted from matching due to the road mismatch.")
    from_matches = matcher.best_last_matches(k=MAX_LATTICE_WIDTH.value)
    matcher.continue_with_distance(from_matches = from_matches, max_dist=MAX_DIST.value)
    matcher.match(path, expand=True)
  
  node_id = matcher.path_pred_onlynodes_withjumps # retrieve the node_ids the route passes through

  id_route = 1
  for i in range(len(node_id)-1):
    route_node = []
    lat = graph.nodes[node_id[i]]['y']
    lon = graph.nodes[node_id[i]]['x']
    latlon = [lat, lon]
    route_node.append(latlon)
    lat2 = graph.nodes[node_id[i+1]]['y']
    lon2 = graph.nodes[node_id[i+1]]['x']
    latlon2 = [lat2, lon2]
    route_node.append(latlon2)
        
    route_node = np.array(route_node)
    df = pd.DataFrame(route_node, columns=['Latitude', 'Longitude'])
    df['id'] = id_route # the same id for one line (street)
    route_df = pd.concat([route_df, df])
    id_route += 1
        
  id += 1

  print("Matching of " + filename + " finished successfully.")
  print("---")

Map matching of test_8.gpx started...
Matching of test_8.gpx finished successfully.
---
Map matching of test_3.gpx started...
Matching of test_3.gpx finished successfully.
---
Map matching of test_7.gpx started...
Matching of test_7.gpx finished successfully.
---
Map matching of test_10.gpx started...
Matching of test_10.gpx finished successfully.
---
Map matching of test_1.gpx started...
Matching of test_1.gpx finished successfully.
---
Map matching of test_6.gpx started...
Matching of test_6.gpx finished successfully.
---
Map matching of test_9.gpx started...
Parts of the path were omitted from matching due to the road mismatch.
Matching of test_9.gpx finished successfully.
---
Map matching of test_4.gpx started...
Matching of test_4.gpx finished successfully.
---
Map matching of test_5.gpx started...
Matching of test_5.gpx finished successfully.
---
Map matching of test_2.gpx started...
Matching of test_2.gpx finished successfully.
---


# **3. Post-processing**

### 2D array of coordinates into GeoDataFrame
Returns a set of LineStrings of tracks and matched routes diferentiated by the ids.

In [ ]:
track_point = gpd.GeoDataFrame(track_df, geometry=gpd.points_from_xy(track_df.Longitude, track_df.Latitude))
track_lines = track_point.groupby(['id']) ['geometry'].apply(lambda x: LineString(x.tolist()))
tracks_gdf = gpd.GeoDataFrame(track_lines, geometry='geometry').set_crs('epsg:4326')
print(tracks_gdf[:10])

                                             geometry
id                                                   
1   LINESTRING (17.27261 49.59848, 17.27240 49.598...
2   LINESTRING (17.27464 49.59808, 17.27482 49.597...
3   LINESTRING (17.27274 49.59826, 17.27239 49.598...
4   LINESTRING (17.27194 49.59764, 17.27163 49.597...
5   LINESTRING (17.25529 49.58775, 17.25511 49.587...
6   LINESTRING (17.27248 49.59870, 17.27249 49.598...
7   LINESTRING (17.27247 49.59812, 17.27245 49.598...
8   LINESTRING (17.27451 49.59822, 17.27454 49.598...
9   LINESTRING (17.27318 49.59829, 17.27334 49.597...
10  LINESTRING (17.25546 49.58794, 17.25529 49.587...


In [ ]:
route_point = gpd.GeoDataFrame(route_df, geometry=gpd.points_from_xy(route_df.Longitude, route_df.Latitude))
route_line = route_point.groupby(['id']) ['geometry'].apply(lambda x: LineString(x.tolist()))
route_gdf = gpd.GeoDataFrame(route_line, geometry='geometry').set_crs('epsg:4326')

print(route_gdf[:10])

                                             geometry
id                                                   
1   LINESTRING (17.27267 49.59851, 17.27268 49.598...
2   LINESTRING (17.27268 49.59853, 17.27239 49.598...
3   LINESTRING (17.27239 49.59862, 17.27244 49.598...
4   LINESTRING (17.27244 49.59868, 17.27251 49.598...
5   LINESTRING (17.27251 49.59876, 17.27238 49.598...
6   LINESTRING (17.27238 49.59881, 17.27232 49.598...
7   LINESTRING (17.27232 49.59883, 17.27228 49.598...
8   LINESTRING (17.27228 49.59884, 17.27234 49.598...
9   LINESTRING (17.27234 49.59892, 17.27237 49.598...
10  LINESTRING (17.27237 49.59896, 17.27240 49.599...


### Calculation of Frequencies
Create the reference Geodataframe from MultiDiGraph and delete unnecessary atributes.

In [ ]:
street_lines = ox.graph_to_gdfs(graph, nodes = False)
street_lines = street_lines.drop(columns=['oneway', 'lanes', 'highway', 'maxspeed',
                                      'reversed', 'bridge', 'name', 'junction',
                                      'service','access', 'tunnel', 'width', 'ref'])
#print(road_lines)

Spatial Filter, intersection of roads and routes, and frequency incrementation based on *covers* function.

Final cleaning: clip roads outside of the study area.

In [ ]:
street_freq = street_lines.overlay(route_gdf, how='intersection') # drop geometries not part of the routes

frequency = []
for _, row in street_freq.iterrows():
  series = route_gdf.covers(row["geometry"])
  frequency.append(series.values.sum())
street_freq["frequency"] = frequency

lines_frequency = gpd.clip(street_freq, study_area, keep_geom_type=True)

In [ ]:
print("The length of matched roads is", round(lines_frequency["length"].sum()), "meters.")

The length of matched roads is 144240.88299999997 meters.


# **4. Visualization**

In [ ]:
m_light = leafmap.Map(width="840", 
                      height="480",
                      draw_control=False,
                      attribution_control=True,
                      tiles="CartoDB positron")

m_light.add_gdf(tracks_gdf,
                layer_name='tracks',
                info_mode=None, 
                style={'color':'blue', 'weight':0.5, 'opacity': 0.5})

m_light.add_data(lines_frequency,
                 "frequency",
                 cmap = "Wistia",
                 scheme='Quantiles',
                 k=5,
                 add_legend=True,
                 legend_title="Number of passages",
                 legend_position="bottomright",
                 layer_name="passages",
                 style_function = lambda feat: {"color": feat["properties"]["color"], 
                                                "weight": 4, 
                                                'opacity': 0.9})
m_light.add_gdf(boundary_sa, 
                layer_name='study area', 
                style={'color':'black', 'weight':3, 'opacity': 0.5})

m_light.zoom_to_gdf(lines_frequency)

m_light


In [ ]:
m_dark = leafmap.Map(width="840", 
                     height="480",
                     draw_control=False,
                     attribution_control=True,
                     tiles="Cartodbdark_matter")
m_dark.add_gdf(tracks_gdf,
               layer_name='tracks',
               info_mode=None, 
               style={'color':'red', 'weight':0.5, 'opacity': 0.5})
m_dark.add_data(lines_frequency,
                "frequency",
                cmap = "YlOrBr_r",
                scheme='Quantiles',
                k=5,
                add_legend=True,
                legend_title="Number of passages",
                legend_position="bottomright",
                layer_name="passages",
                style_function = lambda feat:{"color": feat["properties"]["color"], 
                                              "weight": 4, 
                                              'opacity': 0.8})
m_dark.add_gdf(boundary_sa, 
               layer_name='study area', 
               style={'color':'grey', 'weight':3, 'opacity': 0.5})

m_dark.zoom_to_gdf(lines_frequency)
m_dark


# **5. Save the Results**


In [ ]:
# save the final linear layer with frequences to GeoJSON and GeoPackage file
lines_frequency.to_file(OUTPUT_FOLDER+"/lines_freq.json", driver="GeoJSON")
lines_frequency.to_file(OUTPUT_FOLDER+"/lines_freq.gpkg", driver="GPKG")

In [ ]:
# save the interactive map to html
m_light.to_html(OUTPUT_FOLDER+"/freq_map.html")